## Creación función de scrapeo:

En este jupyter lo que vo a crer es una función que albergue todas las funciones de scrapeo creadas en los otros jupyter para pasarle los links y me haga un proceso de paralelización.

Al solo contar con 8 núcleos, divido los likns en pequeños grupos para que el proceso vaya más rápido.

Una vez obtenido los datos, se me genera una lista de dataframes que posteriormente concateno y guardo en csv. La limpieza de estos csv y su estanderización la realizaré en otro jupyter para no saturar este.

In [1]:
import pandas as pd
import requests as req
from bs4 import BeautifulSoup as bs
import re
import json
import numpy as np
import warnings
warnings.filterwarnings('ignore')
import csv
pd.set_option('display.max_rows', None) 
pd.set_option('display.max_columns', None) 
from selenium import webdriver
import time
%pip install webdriver-manager
from selenium import webdriver
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager

Note: you may need to restart the kernel to use updated packages.


In [2]:
from selenium.webdriver.chrome.options import Options
opciones=Options()
# quita la bandera de ser robot
opciones.add_experimental_option('excludeSwitches', ['enable-automation'])
opciones.add_experimental_option('useAutomationExtension', False)
opciones.headless=False   # si True, no aparece la ventana (headless=no visible)
opciones.add_argument('--start-maximized')         # comienza maximizado
#opciones.add_extension('driver/adblock.crx')       # adblocker
#opciones.add_argument('user-data-dir=selenium')    # mantiene las coockies
opciones.add_argument('--incognito')              # incognito


In [10]:
def tirania(url):
    
    PATH=ChromeDriverManager().install()
    driver=webdriver.Chrome(PATH) 
    driver.get(url)
    time.sleep(8)
    
    
    df=pd.DataFrame(columns=['Beach','Date','Hour','Wind_speed','Gust','Wave','Period','Temperature','Wind_direction','Wave_direction'])
    
    
    date=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_dates"]').text.split()

    lst=[]
    for e in range(0,len(date)+3,3):
        var=''.join(date[e-2]).replace('.','')
        lst.append(var)

    lst.pop(0)  

    for e in range(len(lst)):
        df['Date']=lst

    time.sleep(8)

    hour=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_dates"]').text.split()
    lst2=[]
    for e in range(0,len(date)+3,3):
        var=''.join(date[e-1:e])
        lst2.append(var)
    lst2.pop(0)    
    for e in range(len(lst2)):
        df['Hour']=lst2

    time.sleep(5)

    playa=driver.find_element(By.XPATH, '//*[@id="forecasts-page-content"]/div[2]/div[1]/a[1]/div').text

    for e in range(len(df.Hour)):
        df['Beach']=playa

    time.sleep(4)

    
    velocidad=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_WINDSPD"]').text.split()

    for e in range(len(velocidad)):
        df['Wind_speed']=velocidad

    rafagas=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_GUST"]').text.split()

    for e in range(len(rafagas)):
        df['Gust']=rafagas
    
    ola=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_HTSGW"]').text.split()
    
    
    for e in range(len(ola)):
        if ola=='':
    
            df['Wave']=''
        else:
            df['Wave']=ola

    
    periodo=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_PERPW"]').text.split()

    for e in range(len(periodo)):
        df['Period']=periodo


    
    temp=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_TMP"]').text.split()

    for e in range(len(temp)):
        df['Temperature']=temp

    direc_viento=driver.find_elements(By.XPATH, '//*[@id="tabid_0_0_SMER"]')

    for f in direc_viento:
        elementos=f.find_elements(By.TAG_NAME, 'span')
        tmp=[]

        for e in elementos:
            tmp.append(e.get_attribute('title'))
        tmp.append(url.split('/')[-1])
    

    tmp.pop()
    df['Wind_direction']=tmp

    direc_ola=driver.find_elements(By.XPATH, '//*[@id="tabid_0_0_DIRPW"]')
    

    for f in direc_ola:

        elementos=f.find_elements(By.TAG_NAME, 'span')

        tmp2=[]
        for e in elementos:

            #tmp2.append(e.get_attribute('title'))

            mequetrefe=e.get_attribute('title')

            tmp2.append(mequetrefe)


        if len(mequetrefe)>0:   
            tmp2.append(url.split('/')[-1])

        else:
            mequetrefe=''

    if len(tmp2)>1:
        tmp2.pop()    
        df['Wave_direction']=tmp2
    else:
        df['Wave_direction']=mequetrefe
    

    
        
        
        
        

    
    #time.sleep(8)
    
    #loca=driver.find_element(By.XPATH, '//*[@id="forecasts-page-content"]/div[2]/div[1]/div[2]/ul/li[4]/a').text[:-8]
    
    #for e in range(len(loca)):
        #df['Location']=loca
    
    
  
        
    
  


    return df


In [11]:
    #tirania('https://www.windguru.cz/48686')

In [5]:
%pip install joblib

Note: you may need to restart the kernel to use updated packages.


In [6]:
from joblib import Parallel, delayed

In [13]:

links=['https://www.windguru.cz/48686',
'https://www.windguru.cz/501079',
'https://www.windguru.cz/501080',
'https://www.windguru.cz/696275',
'https://www.windguru.cz/48688',
'https://www.windguru.cz/4903',
'https://www.windguru.cz/48690',
'https://www.windguru.cz/53313']


lst_playas=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:  1.2min remaining:  3.6min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:  1.2min finished


In [14]:
playas=pd.concat(lst_playas)
playas

Beach Date Hour Wind_speed Gust  \
0                              Spain - Hondarribia   15  07h          6   13   
1                              Spain - Hondarribia   15  09h          6   16   
2                              Spain - Hondarribia   15  11h          8   15   
3                              Spain - Hondarribia   15  13h          8   14   
4                              Spain - Hondarribia   15  15h          7   13   
5                              Spain - Hondarribia   15  17h         10   18   
6                              Spain - Hondarribia   15  19h          8   18   
7                              Spain - Hondarribia   15  21h         10   21   
8                              Spain - Hondarribia   16  03h         13   24   
9                              Spain - Hondarribia   16  05h         10   19   
10                             Spain - Hondarribia   16  07h          8   14   
11                             Spain - Hondarribia   16  09h          7   11   
12                             Spain - Hondarribia   16  11h          6   10   
13                             Spain - Hondarribia   16  13h          5    8   
14                             Spain - Hondarribia   16  15h          5    9   
15                             Spain - Hondarribia   16  17h          4    8   
16                             Spain - Hondarribia   16  19h          4    7   
17                             Spain - Hondarribia   16  21h          4    8   
18                             Spain - Hondarribia   17  03h          2    3   
19                             Spain - Hondarribia   17  05h          2    3   
20                             Spain - Hondarribia   17  07h          3    4   
21                             Spain - Hondarribia   17  09h          3    6   
22                             Spain - Hondarribia   17  11h          3    6   
23                             Spain - Hondarribia   17  13h          4    6   
24                             Spain - Hondarribia   17  15h          5    9   
25                             Spain - Hondarribia   17  17h          5    9   
26                             Spain - Hondarribia   17  19h          5   11   
27                             Spain - Hondarribia   17  21h          7   14   
28                             Spain - Hondarribia   18  03h          8   16   
29                             Spain - Hondarribia   18  05h          9   18   
30                             Spain - Hondarribia   18  07h          8   24   
31                             Spain - Hondarribia   18  09h         15   28   
32                             Spain - Hondarribia   18  11h         16   27   
33                             Spain - Hondarribia   18  13h         17   30   
34                             Spain - Hondarribia   18  15h         20   35   
35                             Spain - Hondarribia   18  17h         18   34   
36                             Spain - Hondarribia   18  19h         19   34   
37                             Spain - Hondarribia   18  22h         11   22   
38                             Spain - Hondarribia   19  04h         10   22   
39                             Spain - Hondarribia   19  06h         11   21   
40                             Spain - Hondarribia   19  08h         10   20   
41                             Spain - Hondarribia   19  10h         10   17   
42                             Spain - Hondarribia   19  12h         12   22   
43                             Spain - Hondarribia   19  14h         13   23   
44                             Spain - Hondarribia   19  16h         11   19   
45                             Spain - Hondarribia   19  18h         14   25   
46                             Spain - Hondarribia   19  20h         15   29   
47                             Spain - Hondarribia   19  22h         15   31   
48                             Spain - Hondarribia   20  04h         16   34   
49                             Spain - Hondar

In [15]:
links2=['https://www.windguru.cz/48687',
'https://www.windguru.cz/48689',
'https://www.windguru.cz/48692',
'https://www.windguru.cz/48691',
'https://www.windguru.cz/501076',
'https://www.windguru.cz/47715',
'https://www.windguru.cz/11040',
'https://www.windguru.cz/501082']

links3=['https://www.windguru.cz/48694',
'https://www.windguru.cz/48695',
'https://www.windguru.cz/48696',
'https://www.windguru.cz/48698',
'https://www.windguru.cz/48702',
'https://www.windguru.cz/207059',
'https://www.windguru.cz/48701',
'https://www.windguru.cz/48699']

links4=['https://www.windguru.cz/332103',
'https://www.windguru.cz/48704',
'https://www.windguru.cz/48705',
'https://www.windguru.cz/48706',
'https://www.windguru.cz/48707',
'https://www.windguru.cz/48708',
'https://www.windguru.cz/356406',
'https://www.windguru.cz/501095']

links5=['https://www.windguru.cz/48710',
'https://www.windguru.cz/48711',
'https://www.windguru.cz/501091',
'https://www.windguru.cz/222022',
'https://www.windguru.cz/48713',
'https://www.windguru.cz/501093',
'https://www.windguru.cz/329634']

links6=['https://www.windguru.cz/501096',
'https://www.windguru.cz/501103',
'https://www.windguru.cz/501104',
'https://www.windguru.cz/501105',
'https://www.windguru.cz/501106',
'https://www.windguru.cz/501107',
'https://www.windguru.cz/48716',
'https://www.windguru.cz/356413',
'https://www.windguru.cz/48717',
'https://www.windguru.cz/48718']

links7=['https://www.windguru.cz/48719',
        'https://www.windguru.cz/48720',
        'https://www.windguru.cz/48721',
        'https://www.windguru.cz/212',
        'https://www.windguru.cz/48723',
        'https://www.windguru.cz/48725',
        'https://www.windguru.cz/48726',
        'https://www.windguru.cz/48727',
        'https://www.windguru.cz/48728',
        'https://www.windguru.cz/501108']



linksCN=['https://www.windguru.cz/103501',
         'https://www.windguru.cz/73233',
'https://www.windguru.cz/501283',
'https://www.windguru.cz/49328',
'https://www.windguru.cz/501286',
'https://www.windguru.cz/501281',
'https://www.windguru.cz/49337',  
'https://www.windguru.cz/49335',
'https://www.windguru.cz/49334']
        
       



In [16]:
lst_playas2=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links2)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:  1.1min remaining:  3.3min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:  1.2min finished


In [17]:
playas2=pd.concat(lst_playas2)
playas2

Beach Date Hour Wind_speed Gust Wave Period  \
0            Spain - Zurriola   15  07h          5   10    1     14   
1            Spain - Zurriola   15  09h          6   15    1     14   
2            Spain - Zurriola   15  11h          8   15    1     13   
3            Spain - Zurriola   15  13h          7   12  0.9     13   
4            Spain - Zurriola   15  15h          8   11  1.1     13   
5            Spain - Zurriola   15  17h         11   17  1.1     12   
6            Spain - Zurriola   15  19h          9   17  1.1     11   
7            Spain - Zurriola   15  21h         11   18  1.5      6   
8            Spain - Zurriola   16  03h         15   22    2      8   
9            Spain - Zurriola   16  05h         12   18    2      8   
10           Spain - Zurriola   16  07h         10   16  1.9      7   
11           Spain - Zurriola   16  09h          8   12  1.8      7   
12           Spain - Zurriola   16  11h          8   11  1.7      7   
13           Spain - Zurriola   16  13h          6   10  1.6      7   
14           Spain - Zurriola   16  15h          7   10  1.5      7   
15           Spain - Zurriola   16  17h          5    9  1.5      7   
16           Spain - Zurriola   16  19h          5    8  1.4      7   
17           Spain - Zurriola   16  21h          5    8  1.3      7   
18           Spain - Zurriola   17  03h          2    2    1      6   
19           Spain - Zurriola   17  05h          3    3  0.9      6   
20           Spain - Zurriola   17  07h          3    4  0.8      6   
21           Spain - Zurriola   17  09h          4    6  0.8      6   
22           Spain - Zurriola   17  11h          3    6  0.7      6   
23           Spain - Zurriola   17  13h          3    5  0.6      6   
24           Spain - Zurriola   17  15h          4    8  0.6      5   
25           Spain - Zurriola   17  17h          3    8  0.5      5   
26           Spain - Zurriola   17  19h          5   10  0.5      5   
27           Spain - Zurriola   17  21h          9   13  0.5      6   
28           Spain - Zurriola   18  03h          9   15  0.5     15   
29           Spain - Zurriola   18  05h         10   17  0.6     14   
30           Spain - Zurriola   18  07h         11   25  0.6      4   
31           Spain - Zurriola   18  09h         15   29  0.7      4   
32           Spain - Zurriola   18  11h         16   29  0.7      4   
33           Spain - Zurriola   18  13h         17   30  0.8      4   
34           Spain - Zurriola   18  15h         18   31  0.8      4   
35           Spain - Zurriola   18  17h         18   32  0.8      4   
36           Spain - Zurriola   18  19h         18   32  0.9      4   
37           Spain - Zurriola   18  22h         11   22  0.9      4   
38           Spain - Zurriola   19  04h         11   22  0.8      4   
39           Spain - Zurriola   19  06h         11   23  0.9      4   
40           Spain - Zurriola   19  08h         12   23  0.8      4   
41           Spain - Zurriola   19  10h         12   24  0.8      4   
42           Spain - Zurriola   19  12h         12   25    1      4   
43           Spain - Zurriola   19  14h         12   25    1      8   
44           Spain - Zurriola   19  16h         11   22  0.8     17   
45           Spain - Zurriola   19  18h         14   27  0.8     17   
46           Spain - Zurriola   19  20h         16   30  0.9     16   
47           Spain - Zurriola   19  22h         16   33    1     15   
48           Spain - Zurriola   20  04h         15   31  1.2     15   
49           Spain - Zurriola   20  06h         13   21  1.1     15   
50           Spain - Zurriola   20  08h         14   38  1.1     15   
51           Spain - Zurriola   20  10h         19   41    1     14   
52           Spain - Zurriola   20  12h         17   36  0.9     14   
53           Spain - Zurriola   20  14h         10   28  0.9     14   
54           Spain - Zurriola   20  16h         10   28  0.9     14   
55           Spain - Zurriola   20  18h         

In [19]:
lst_playas3=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links3)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:  1.1min remaining:  3.2min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:  1.2min finished


In [20]:
playas3=pd.concat(lst_playas3)
playas3

Beach Date Hour Wind_speed Gust Wave Period  \
0                         Spain - Somo   15  07h          5    8  1.1     13   
1                         Spain - Somo   15  09h          5    8    1     13   
2                         Spain - Somo   15  11h          6    9    1     13   
3                         Spain - Somo   15  13h          9   14  1.1     12   
4                         Spain - Somo   15  15h         11   17  1.2     12   
5                         Spain - Somo   15  17h         11   20  1.2     10   
6                         Spain - Somo   15  19h         12   17  1.3      5   
7                         Spain - Somo   15  21h         11   16  1.3      6   
8                         Spain - Somo   16  03h          9   13  1.8      8   
9                         Spain - Somo   16  05h         10   14  1.8      8   
10                        Spain - Somo   16  07h         11   16  1.8      8   
11                        Spain - Somo   16  09h         10   15  1.9      8   
12                        Spain - Somo   16  11h         10   15  1.9      8   
13                        Spain - Somo   16  13h          8   13  1.8      8   
14                        Spain - Somo   16  15h          9   13  1.8      8   
15                        Spain - Somo   16  17h          7   12  1.7      8   
16                        Spain - Somo   16  19h          5    9  1.6      7   
17                        Spain - Somo   16  21h          5    7  1.5      7   
18                        Spain - Somo   17  03h          5    7  1.2      6   
19                        Spain - Somo   17  05h          5    8  1.1      6   
20                        Spain - Somo   17  07h          6   10  1.1      6   
21                        Spain - Somo   17  09h          6    9    1      6   
22                        Spain - Somo   17  11h          5    9  0.9      6   
23                        Spain - Somo   17  13h          5    8  0.8      6   
24                        Spain - Somo   17  15h          4    6  0.8      6   
25                        Spain - Somo   17  17h          2    4  0.7      5   
26                        Spain - Somo   17  19h          4    4  0.7      5   
27                        Spain - Somo   17  21h          5    6  0.6     13   
28                        Spain - Somo   18  03h          6   13  0.5     12   
29                        Spain - Somo   18  05h          6   15  0.5     12   
30                        Spain - Somo   18  07h         11   27  0.5     14   
31                        Spain - Somo   18  09h         17   31  0.7     10   
32                        Spain - Somo   18  11h         20   35  0.8      7   
33                        Spain - Somo   18  13h         19   35  1.1      4   
34                        Spain - Somo   18  15h         21   38  1.2      4   
35                        Spain - Somo   18  17h         21   38  1.2      5   
36                        Spain - Somo   18  19h         17   34  1.2      5   
37                        Spain - Somo   18  22h         13   29  1.2      5   
38                        Spain - Somo   19  04h         10   25  1.2      5   
39                        Spain - Somo   19  06h         10   24  1.2      5   
40                        Spain - Somo   19  08h         10   24  1.4      5   
41                        Spain - Somo   19  10h         10   24  1.6      5   
42                        Spain - Somo   19  12h         12   29  1.6      5   
43                        Spain - Somo   19  14h         13   31  1.5      5   
44                        Spain - Somo   19  16h         15   32  1.4      5   
45                        Spain - Somo   19  18h         16   33  1.4     11   
46                        Spain - Somo   19  20h         15   32  1.4     14   
47                        Spain - Somo   19  22h         14   28  1.5     15   
48                        Spain - Somo   20  04h         10   20  1.6     15   
49                        Spain -

In [22]:
lst_playas4=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links4)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:  1.1min remaining:  3.4min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:  1.3min finished


In [23]:
playas4=pd.concat(lst_playas4)
playas4

Beach Date Hour Wind_speed Gust Wave Period  \
0            Spain - Ribadesella   15  07h          7   10  0.9     13   
1            Spain - Ribadesella   15  09h          6   11    1     12   
2            Spain - Ribadesella   15  11h          5    9    1     12   
3            Spain - Ribadesella   15  13h          4   11  0.9     12   
4            Spain - Ribadesella   15  15h          7   11  0.9     12   
5            Spain - Ribadesella   15  17h          5   10    1     11   
6            Spain - Ribadesella   15  19h          5    7  1.1     10   
7            Spain - Ribadesella   15  21h          6   13  1.1      8   
8            Spain - Ribadesella   16  03h          7   11  1.9      8   
9            Spain - Ribadesella   16  05h         11   16    2      8   
10           Spain - Ribadesella   16  07h         13   20  2.1      8   
11           Spain - Ribadesella   16  09h         13   20  2.2      8   
12           Spain - Ribadesella   16  11h         13   21  2.2      8   
13           Spain - Ribadesella   16  13h         10   19  2.1      8   
14           Spain - Ribadesella   16  15h         12   19  2.1      8   
15           Spain - Ribadesella   16  17h         11   18    2      8   
16           Spain - Ribadesella   16  19h         10   18  1.9      8   
17           Spain - Ribadesella   16  21h          9   15  1.8      8   
18           Spain - Ribadesella   17  03h          7   13  1.4      7   
19           Spain - Ribadesella   17  05h          7   12  1.4      7   
20           Spain - Ribadesella   17  07h          6   10  1.3      6   
21           Spain - Ribadesella   17  09h          4    8  1.2      6   
22           Spain - Ribadesella   17  11h          3    6  1.1      6   
23           Spain - Ribadesella   17  13h          4    5    1      6   
24           Spain - Ribadesella   17  15h          3    5  0.9      6   
25           Spain - Ribadesella   17  17h          3    5  0.9      6   
26           Spain - Ribadesella   17  19h          4    5  0.8      6   
27           Spain - Ribadesella   17  21h          6    9  0.7      6   
28           Spain - Ribadesella   18  03h          7   15  0.6      5   
29           Spain - Ribadesella   18  05h          8   16  0.6     12   
30           Spain - Ribadesella   18  07h         10   26  0.6     12   
31           Spain - Ribadesella   18  09h         14   27  0.5     12   
32           Spain - Ribadesella   18  11h         15   29  0.5     12   
33           Spain - Ribadesella   18  13h         17   31  0.5     12   
34           Spain - Ribadesella   18  15h         20   33  0.5     12   
35           Spain - Ribadesella   18  17h         19   33  0.6     10   
36           Spain - Ribadesella   18  19h         17   29  0.7      5   
37           Spain - Ribadesella   18  22h          8   12  0.9      5   
38           Spain - Ribadesella   19  04h          5    6  0.7     11   
39           Spain - Ribadesella   19  06h          5    7  0.7     12   
40           Spain - Ribadesella   19  08h          5    7  0.7     14   
41           Spain - Ribadesella   19  10h          4    7  0.7     18   
42           Spain - Ribadesella   19  12h          5    9  0.7     17   
43           Spain - Ribadesella   19  14h          6    9  0.8     16   
44           Spain - Ribadesella   19  16h          5    8  0.9     15   
45           Spain - Ribadesella   19  18h          6    8  0.9     15   
46           Spain - Ribadesella   19  20h          6    9  0.9     15   
47           Spain - Ribadesella   19  22h          6    8    1     15   
48           Spain - Ribadesella   20  04h          6    8  1.2     14   
49           Spain - Ribadesella   20  06h          7    6  1.2     14   
50           Spain - Ribadesella   20  08h          6   25  1.1     14   
51           Spain - Ribadesella   20  10h          9   11    1     14   
52           Spain - Ribadesella   20  12h         13   33    1     14   
53           Spain - Ribadesell

In [24]:
lst_playas5=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links5)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   7 out of   7 | elapsed:  1.0min finished


In [25]:
playas5=pd.concat(lst_playas5)
playas5

Beach Date Hour Wind_speed Gust Wave Period  \
0              Spain - Salinas   15  07h          3    6  1.4     12   
1              Spain - Salinas   15  09h          3    6  1.2     12   
2              Spain - Salinas   15  11h          2    5  1.2     12   
3              Spain - Salinas   15  13h          3    7  1.2     11   
4              Spain - Salinas   15  15h          4    8  1.3     11   
5              Spain - Salinas   15  17h          4    8  1.4     11   
6              Spain - Salinas   15  19h          3    4  1.5     10   
7              Spain - Salinas   15  21h          3    6  1.6     10   
8              Spain - Salinas   16  03h          5   11  2.2      9   
9              Spain - Salinas   16  05h          7   13  2.3      9   
10             Spain - Salinas   16  07h          8   16  2.5      9   
11             Spain - Salinas   16  09h         10   20  2.5      9   
12             Spain - Salinas   16  11h         10   20  2.5      8   
13             Spain - Salinas   16  13h          9   18  2.4      8   
14             Spain - Salinas   16  15h         10   19  2.3      8   
15             Spain - Salinas   16  17h          8   18  2.2      8   
16             Spain - Salinas   16  19h          7   16  2.1      8   
17             Spain - Salinas   16  21h          6   15    2      8   
18             Spain - Salinas   17  03h          5   11  1.6      7   
19             Spain - Salinas   17  05h          4   10  1.5      7   
20             Spain - Salinas   17  07h          4    5  1.3      7   
21             Spain - Salinas   17  09h          4    6  1.2      6   
22             Spain - Salinas   17  11h          2    5  1.1      6   
23             Spain - Salinas   17  13h          2    4  1.1      6   
24             Spain - Salinas   17  15h          3    4    1      6   
25             Spain - Salinas   17  17h          3    5  0.9      6   
26             Spain - Salinas   17  19h          4    5  0.9      6   
27             Spain - Salinas   17  21h          5    7  0.8      6   
28             Spain - Salinas   18  03h          5    9  0.8     14   
29             Spain - Salinas   18  05h          5   11  0.8     13   
30             Spain - Salinas   18  07h          5   14  0.7     13   
31             Spain - Salinas   18  09h          4    7  0.7     13   
32             Spain - Salinas   18  11h          5   18  0.7     13   
33             Spain - Salinas   18  13h          8   21  0.8     13   
34             Spain - Salinas   18  15h          6   22  0.9     11   
35             Spain - Salinas   18  17h          7   16    1     10   
36             Spain - Salinas   18  19h          7   16  1.1      8   
37             Spain - Salinas   18  22h          5   10  1.1      6   
38             Spain - Salinas   19  04h          5   10  1.2     11   
39             Spain - Salinas   19  06h          5   10  1.1     15   
40             Spain - Salinas   19  08h          5   10  1.2     17   
41             Spain - Salinas   19  10h          5    9  1.2     17   
42             Spain - Salinas   19  12h          4   11  1.3     16   
43             Spain - Salinas   19  14h          5   11  1.3     16   
44             Spain - Salinas   19  16h          5   10  1.5     15   
45             Spain - Salinas   19  18h          5   10  1.6     15   
46             Spain - Salinas   19  20h          5    9  1.6     15   
47             Spain - Salinas   19  22h          5   10  1.7     15   
48             Spain - Salinas   20  04h          3    5  1.6     14   
49             Spain - Salinas   20  06h          5    6  1.5     14   
50             Spain - Salinas   20  08h          7   15  1.5     14   
51             Spain - Salinas   20  10h          7   11  1.5     14   
52             Spain - Salinas   20  12h          4   26  1.8     14   
53             Spain - Salinas   20  14h         13   22  2.1     13   
54             Spain - Salinas   20  16h          8   14  2.2    

In [26]:
lst_playas6=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links6)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   6 out of  10 | elapsed:  1.1min remaining:   45.2s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:  1.8min finished


In [27]:
playas6=pd.concat(lst_playas6)
playas6

Beach Date Hour Wind_speed Gust Wave Period Temperature  \
0   Spain - Foz, La Charca   15  07h          4   10  1.2     12          12   
1   Spain - Foz, La Charca   15  09h          6   12  1.2     12          13   
2   Spain - Foz, La Charca   15  11h          9   15  1.2     12          13   
3   Spain - Foz, La Charca   15  13h         10   16  1.2     11          14   
4   Spain - Foz, La Charca   15  15h          7   14  1.2     11          14   
5   Spain - Foz, La Charca   15  17h          4    9  1.3     11          14   
6   Spain - Foz, La Charca   15  19h          3    5  1.6     11          13   
7   Spain - Foz, La Charca   15  21h          2    3  1.8     10          13   
8   Spain - Foz, La Charca   16  03h          5    7  2.3     10          12   
9   Spain - Foz, La Charca   16  05h          7   11  2.4     10          11   
10  Spain - Foz, La Charca   16  07h         15   23  2.6     10          12   
11  Spain - Foz, La Charca   16  09h         21   29  2.8      9          12   
12  Spain - Foz, La Charca   16  11h         20   29  2.8      9          12   
13  Spain - Foz, La Charca   16  13h         19   27  2.7      9          12   
14  Spain - Foz, La Charca   16  15h         19   26  2.6      8          12   
15  Spain - Foz, La Charca   16  17h         18   26  2.5      8          12   
16  Spain - Foz, La Charca   16  19h         17   24  2.4      8          12   
17  Spain - Foz, La Charca   16  21h         10   18  2.3      8          10   
18  Spain - Foz, La Charca   17  03h          5    7  1.8      7           8   
19  Spain - Foz, La Charca   17  05h          4    6  1.7      7           7   
20  Spain - Foz, La Charca   17  07h          5    7  1.5      7           7   
21  Spain - Foz, La Charca   17  09h          6    9  1.4      7           8   
22  Spain - Foz, La Charca   17  11h          5    9  1.3      7          10   
23  Spain - Foz, La Charca   17  13h          4   10  1.2      6          13   
24  Spain - Foz, La Charca   17  15h          4    9  1.1      6          14   
25  Spain - Foz, La Charca   17  17h          4    8    1      6          14   
26  Spain - Foz, La Charca   17  19h          5    8  0.9      6          12   
27  Spain - Foz, La Charca   17  21h          5   12  0.9      6          11   
28  Spain - Foz, La Charca   18  03h         11   26  0.8      6          13   
29  Spain - Foz, La Charca   18  05h         15   32  0.7      6          13   
30  Spain - Foz, La Charca   18  07h         15   36  0.7      6          14   
31  Spain - Foz, La Charca   18  09h         22   42  0.8      6          15   
32  Spain - Foz, La Charca   18  11h         24   44    1      5          15   
33  Spain - Foz, La Charca   18  13h         24   44  1.2      4          16   
34  Spain - Foz, La Charca   18  15h         25   44  1.1      7          16   
35  Spain - Foz, La Charca   18  17h         16   38  1.1      9          16   
36  Spain - Foz, La Charca   18  19h         12   35  1.1      8          16   
37  Spain - Foz, La Charca   18  22h         16   34  1.1     10          16   
38  Spain - Foz, La Charca   19  04h         15   34  1.1     11          16   
39  Spain - Foz, La Charca   19  06h         15   34  1.2     14          16   
40  Spain - Foz, La Charca   19  08h         15   33  1.3     16          16   
41  Spain - Foz, La Charca   19  10h         14   32  1.4     16          16   
42  Spain - Foz, La Charca   19  12h         14   33  1.5     15          17   
43  Spain - Foz, La Charca   19  14h         15   33  1.5     15          17   
44  Spain - Foz, La Charca   19  16h         16   34  1.6     15          17   
45  Spain - Foz, La Charca   19  18h         15   34  1.6     15          17   
46  Spain - Foz, La Charca   19  20h         14   33  1.6     14          17   
47  Spain - Foz, La Charca   19  22h         13   33  1.6     14          17   
48  Spain - Foz, La Charca   20  04h         11   29  1.5     14          17   
49  Spain - Foz, La C

In [28]:
lst_playas7=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links7)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   6 out of  10 | elapsed:  1.2min remaining:   49.7s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:  1.9min finished


In [29]:
playas7=pd.concat(lst_playas7)
playas7

Beach Date Hour Wind_speed Gust Wave Period  \
0            Spain - Santa Comba   15  07h          8   12  2.4     12   
1            Spain - Santa Comba   15  09h         10   17  2.3     11   
2            Spain - Santa Comba   15  11h         11   18  2.3     11   
3            Spain - Santa Comba   15  13h         10   17  2.3     11   
4            Spain - Santa Comba   15  15h          8   14  2.4     11   
5            Spain - Santa Comba   15  17h          7   12  2.5     11   
6            Spain - Santa Comba   15  19h          7   12  2.7     11   
7            Spain - Santa Comba   15  21h          4    8  2.9     11   
8            Spain - Santa Comba   16  03h          3    5  3.1     11   
9            Spain - Santa Comba   16  05h          8   11  3.2     10   
10           Spain - Santa Comba   16  07h         14   21  3.2     10   
11           Spain - Santa Comba   16  09h         20   30  3.3     10   
12           Spain - Santa Comba   16  11h         18   27    3     10   
13           Spain - Santa Comba   16  13h         16   23  2.7      9   
14           Spain - Santa Comba   16  15h         16   22  2.6      9   
15           Spain - Santa Comba   16  17h         16   23  2.4      9   
16           Spain - Santa Comba   16  19h         13   24  2.3      8   
17           Spain - Santa Comba   16  21h         10   18  2.2      8   
18           Spain - Santa Comba   17  03h          4    8  1.6      8   
19           Spain - Santa Comba   17  05h          4    7  1.5      7   
20           Spain - Santa Comba   17  07h          7    9  1.3      7   
21           Spain - Santa Comba   17  09h          7   10  1.2      7   
22           Spain - Santa Comba   17  11h          7   11  1.2      7   
23           Spain - Santa Comba   17  13h          8   12  1.1      7   
24           Spain - Santa Comba   17  15h          8   12  1.1      7   
25           Spain - Santa Comba   17  17h          7   13  1.1      7   
26           Spain - Santa Comba   17  19h          9   16    1     14   
27           Spain - Santa Comba   17  21h          9   18    1     14   
28           Spain - Santa Comba   18  03h         15   29  1.5     13   
29           Spain - Santa Comba   18  05h         17   33  1.7      6   
30           Spain - Santa Comba   18  07h         19   37  1.9      6   
31           Spain - Santa Comba   18  09h         22   41  2.2      7   
32           Spain - Santa Comba   18  11h         24   42  2.5      8   
33           Spain - Santa Comba   18  13h         23   41    3      8   
34           Spain - Santa Comba   18  15h         24   42  2.7      8   
35           Spain - Santa Comba   18  17h         23   41  2.6      9   
36           Spain - Santa Comba   18  19h         23   42  2.7      9   
37           Spain - Santa Comba   18  22h         21   37  2.8     10   
38           Spain - Santa Comba   19  04h         23   39  3.2     11   
39           Spain - Santa Comba   19  06h         22   39  3.5     11   
40           Spain - Santa Comba   19  08h         22   39  3.6     11   
41           Spain - Santa Comba   19  10h         22   38  3.8     12   
42           Spain - Santa Comba   19  12h         21   37  3.7     13   
43           Spain - Santa Comba   19  14h         20   35  3.7     13   
44           Spain - Santa Comba   19  16h         19   34  3.8     14   
45           Spain - Santa Comba   19  18h         18   32  3.7     14   
46           Spain - Santa Comba   19  20h         17   31  3.6     14   
47           Spain - Santa Comba   19  22h         18   31  3.6     14   
48           Spain - Santa Comba   20  04h         15   27  3.3     13   
49           Spain - Santa Comba   20  06h         12   23  3.2     13   
50           Spain - Santa Comba   20  08h         18   32  3.2     13   
51           Spain - Santa Comba   20  10h         18   23  3.3     13   
52           Spain - Santa Comba   20  12h         12   16  3.2     13   
53           Spain - Santa Comb

In [30]:
lst_playasCN=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksCN)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   4 out of   9 | elapsed:  1.2min remaining:  1.5min
[Parallel(n_jobs=-1)]: Done   9 out of   9 | elapsed:  1.7min finished


In [31]:
playasCN=pd.concat(lst_playasCN)
playasCN

Beach Date Hour Wind_speed Gust Wave Period  \
0   Spain - Puerto de la Cruz   15  06h          3    5  2.3     12   
1   Spain - Puerto de la Cruz   15  08h          3    5  2.4     12   
2   Spain - Puerto de la Cruz   15  10h          4    6  2.6     12   
3   Spain - Puerto de la Cruz   15  12h          6    7  2.6     12   
4   Spain - Puerto de la Cruz   15  14h          5    6  2.7     12   
5   Spain - Puerto de la Cruz   15  16h          5    6  2.7     12   
6   Spain - Puerto de la Cruz   15  18h          3    5  2.7     12   
7   Spain - Puerto de la Cruz   15  20h          2    4  2.7     12   
8   Spain - Puerto de la Cruz   15  22h          2    4  2.7     12   
9   Spain - Puerto de la Cruz   16  03h          2    4  2.8     12   
10  Spain - Puerto de la Cruz   16  05h          2    3  2.9     12   
11  Spain - Puerto de la Cruz   16  07h          2    3  2.9     13   
12  Spain - Puerto de la Cruz   16  09h          1    2  2.9     13   
13  Spain - Puerto de la Cruz   16  11h          4    3  2.9     13   
14  Spain - Puerto de la Cruz   16  13h          5    5  2.9     13   
15  Spain - Puerto de la Cruz   16  15h          5    5  2.8     13   
16  Spain - Puerto de la Cruz   16  17h          3    4  2.7     13   
17  Spain - Puerto de la Cruz   16  19h          2    2  2.6     13   
18  Spain - Puerto de la Cruz   16  21h          2    2  2.4     13   
19  Spain - Puerto de la Cruz   17  03h          3    4  2.2     13   
20  Spain - Puerto de la Cruz   17  05h          3    5  2.1     13   
21  Spain - Puerto de la Cruz   17  07h          4    6    2     13   
22  Spain - Puerto de la Cruz   17  09h          4    6    2     13   
23  Spain - Puerto de la Cruz   17  11h          4    6  1.9     13   
24  Spain - Puerto de la Cruz   17  13h          5    6  1.9     13   
25  Spain - Puerto de la Cruz   17  15h          6    5  1.8     13   
26  Spain - Puerto de la Cruz   17  17h          3    4  1.8     13   
27  Spain - Puerto de la Cruz   17  19h          2    3  1.7     13   
28  Spain - Puerto de la Cruz   17  21h          3    4  1.7     13   
29  Spain - Puerto de la Cruz   18  03h          2    3  1.5     12   
30  Spain - Puerto de la Cruz   18  05h          2    3  1.5     12   
31  Spain - Puerto de la Cruz   18  09h          2    4  1.4     11   
32  Spain - Puerto de la Cruz   18  12h          4    5  1.3     11   
33  Spain - Puerto de la Cruz   18  15h          5    6  1.3     11   
34  Spain - Puerto de la Cruz   18  18h          3    5  1.6     17   
35  Spain - Puerto de la Cruz   18  21h          3    4    2     17   
36  Spain - Puerto de la Cruz   19  03h          3    4  2.5     16   
37  Spain - Puerto de la Cruz   19  06h          2    4  2.5     15   
38  Spain - Puerto de la Cruz   19  09h          3    4  2.5     15   
39  Spain - Puerto de la Cruz   19  12h          5    6  2.5     15   
40  Spain - Puerto de la Cruz   19  15h          6    8  2.5     15   
41  Spain - Puerto de la Cruz   19  18h          2    7  2.5     15   
42  Spain - Puerto de la Cruz   19  21h          4    4  2.5     15   
43  Spain - Puerto de la Cruz   20  03h          2    5  2.3     14   
44  Spain - Puerto de la Cruz   20  06h          1    5  2.2     14   
45  Spain - Puerto de la Cruz   20  09h          2    3  2.1     13   
46  Spain - Puerto de la Cruz   20  12h          5    6  2.1     13   
47  Spain - Puerto de la Cruz   20  15h          4    6    2     13   
48  Spain - Puerto de la Cruz   20  18h          3    5  1.9     12   
49  Spain - Puerto de la Cruz   20  21h          5    6  1.8     12   
50  Spain - Puerto de la Cruz   21  03h          5    7  1.7     12   
51  Spain - Puerto de la Cruz   21  06h          5    7  1.7     12   
52  Spain - Puerto de la Cruz   21  09h          4    8  1.7     12   
53  Spain - Puerto de la Cruz   21  12h          7    9  1.8     13   
54  Spain - Puerto de la Cruz   21  15h          6    8  1.9     17   
55  Spain - Puerto de la Cruz   21  18h         

In [69]:
Hendaya=tirania('https://www.windguru.cz/48576')

In [70]:
Hendaya=pd.DataFrame(Hendaya)
Hendaya

Beach Date Hour Wind_speed Gust Wave Period Temperature  \
0   France - Hendaye   15  07h          7   13  1.1     14          13   
1   France - Hendaye   15  09h          6   15  1.1     14          12   
2   France - Hendaye   15  11h          8   15    1     13          15   
3   France - Hendaye   15  13h          8   14  1.1     13          15   
4   France - Hendaye   15  15h          7   12  1.1     13          15   
5   France - Hendaye   15  17h         10   17  1.2     12          13   
6   France - Hendaye   15  19h          8   16  1.2     12          13   
7   France - Hendaye   15  21h         10   19  1.4      5          13   
8   France - Hendaye   16  03h         14   22  2.1      8          12   
9   France - Hendaye   16  05h         11   18  2.1      8          10   
10  France - Hendaye   16  07h          9   14    2      8          10   
11  France - Hendaye   16  09h          7   11  1.8      8           9   
12  France - Hendaye   16  11h          6   10  1.7      8           9   
13  France - Hendaye   16  13h          5    8  1.6      8           9   
14  France - Hendaye   16  15h          6    9  1.5      8           9   
15  France - Hendaye   16  17h          5    8  1.4      7           8   
16  France - Hendaye   16  19h          4    7  1.3      7           8   
17  France - Hendaye   16  21h          4    8  1.2      7           8   
18  France - Hendaye   17  03h          2    3  0.9      6           6   
19  France - Hendaye   17  05h          2    3  0.8      6           6   
20  France - Hendaye   17  07h          4    5  0.7      6           5   
21  France - Hendaye   17  09h          4    7  0.7      6           5   
22  France - Hendaye   17  11h          3    6  0.6      6           7   
23  France - Hendaye   17  13h          4    6  0.5      5           9   
24  France - Hendaye   17  15h          5    8  0.5      5          11   
25  France - Hendaye   17  17h          5    9  0.4     16          10   
26  France - Hendaye   17  19h          5   11  0.4     16           9   
27  France - Hendaye   17  21h          7   13  0.4     15           9   
28  France - Hendaye   18  03h          8   16  0.3     15          10   
29  France - Hendaye   18  05h          9   18  0.4     14          11   
30  France - Hendaye   18  07h          8   24  0.4     14          11   
31  France - Hendaye   18  09h         17   29  0.5     14          13   
32  France - Hendaye   18  11h         17   29  0.5     14          14   
33  France - Hendaye   18  13h         18   31  0.6     14          15   
34  France - Hendaye   18  15h         21   35  0.6     13          15   
35  France - Hendaye   18  17h         19   34  0.6     13          15   
36  France - Hendaye   18  19h         19   34  0.5     13          16   
37  France - Hendaye   18  22h         11   22  0.5     13          15   
38  France - Hendaye   19  04h         10   22  0.7     12          15   
39  France - Hendaye   19  06h         11   21  0.7     12          15   
40  France - Hendaye   19  08h         10   20  0.7     12          15   
41  France - Hendaye   19  10h         10   17  0.7     11          15   
42  France - Hendaye   19  12h         12   22  0.7     12          16   
43  France - Hendaye   19  14h         13   23  0.7     14          17   
44  France - Hendaye   19  16h         11   19  0.8     18          17   
45  France - Hendaye   19  18h         14   25  0.8     17          16   
46  France - Hendaye   19  20h         15   29  0.9     16          16   
47  France - Hendaye   19  22h         15   31    1     16          16   
48  France - Hendaye   20  04h         16   34    1     15          16   
49  France - Hendaye   20  06h         12   18  1.1     15          14   
50  France - Hendaye   20  08h         22   42  1.2     15          15   
51  France - Hendaye   20  10h         23   42  1.3     15          15   
52  France - Hendaye   20  12h         16   35  1.3     15          17   
53  France - Henday

In [71]:
playasN= pd.concat([playas, playas2, playas3, playas4, playas5, playas6, playas7, playasCN, Hendaya], axis=0)
playasN

Beach Date Hour Wind_speed Gust  \
0                              Spain - Hondarribia   15  07h          6   13   
1                              Spain - Hondarribia   15  09h          6   16   
2                              Spain - Hondarribia   15  11h          8   15   
3                              Spain - Hondarribia   15  13h          8   14   
4                              Spain - Hondarribia   15  15h          7   13   
5                              Spain - Hondarribia   15  17h         10   18   
6                              Spain - Hondarribia   15  19h          8   18   
7                              Spain - Hondarribia   15  21h         10   21   
8                              Spain - Hondarribia   16  03h         13   24   
9                              Spain - Hondarribia   16  05h         10   19   
10                             Spain - Hondarribia   16  07h          8   14   
11                             Spain - Hondarribia   16  09h          7   11   
12                             Spain - Hondarribia   16  11h          6   10   
13                             Spain - Hondarribia   16  13h          5    8   
14                             Spain - Hondarribia   16  15h          5    9   
15                             Spain - Hondarribia   16  17h          4    8   
16                             Spain - Hondarribia   16  19h          4    7   
17                             Spain - Hondarribia   16  21h          4    8   
18                             Spain - Hondarribia   17  03h          2    3   
19                             Spain - Hondarribia   17  05h          2    3   
20                             Spain - Hondarribia   17  07h          3    4   
21                             Spain - Hondarribia   17  09h          3    6   
22                             Spain - Hondarribia   17  11h          3    6   
23                             Spain - Hondarribia   17  13h          4    6   
24                             Spain - Hondarribia   17  15h          5    9   
25                             Spain - Hondarribia   17  17h          5    9   
26                             Spain - Hondarribia   17  19h          5   11   
27                             Spain - Hondarribia   17  21h          7   14   
28                             Spain - Hondarribia   18  03h          8   16   
29                             Spain - Hondarribia   18  05h          9   18   
30                             Spain - Hondarribia   18  07h          8   24   
31                             Spain - Hondarribia   18  09h         15   28   
32                             Spain - Hondarribia   18  11h         16   27   
33                             Spain - Hondarribia   18  13h         17   30   
34                             Spain - Hondarribia   18  15h         20   35   
35                             Spain - Hondarribia   18  17h         18   34   
36                             Spain - Hondarribia   18  19h         19   34   
37                             Spain - Hondarribia   18  22h         11   22   
38                             Spain - Hondarribia   19  04h         10   22   
39                             Spain - Hondarribia   19  06h         11   21   
40                             Spain - Hondarribia   19  08h         10   20   
41                             Spain - Hondarribia   19  10h         10   17   
42                             Spain - Hondarribia   19  12h         12   22   
43                             Spain - Hondarribia   19  14h         13   23   
44                             Spain - Hondarribia   19  16h         11   19   
45                             Spain - Hondarribia   19  18h         14   25   
46                             Spain - Hondarribia   19  20h         15   29   
47                             Spain - Hondarribia   19  22h         15   31   
48                             Spain - Hondarribia   20  04h         16   34   
49                             Spain - Hondar

In [72]:
playasN.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasN.csv', index=False, index_label=False)


In [41]:
linksO=['https://www.windguru.cz/48730',
       'https://www.windguru.cz/48731',
       'https://www.windguru.cz/501109',
       'https://www.windguru.cz/501110',
       'https://www.windguru.cz/48733',
       'https://www.windguru.cz/48735',
       'https://www.windguru.cz/48736',
       'https://www.windguru.cz/501116',
       'https://www.windguru.cz/501118',
       'https://www.windguru.cz/128497',
       'https://www.windguru.cz/718895',
       'https://www.windguru.cz/501119',
       'https://www.windguru.cz/501120',
       'https://www.windguru.cz/48738',
       'https://www.windguru.cz/153771',
        'https://www.windguru.cz/501113',
       'https://www.windguru.cz/501114',
       'https://www.windguru.cz/501115',
       'https://www.windguru.cz/48739',
       'https://www.windguru.cz/48741',
       'https://www.windguru.cz/1066',
       'https://www.windguru.cz/48742',
       'https://www.windguru.cz/48743']

In [42]:
lst_playasO=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksO)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  23 out of  23 | elapsed:  3.3min finished


In [43]:
playasO=pd.concat(lst_playasO)
playasO

Beach Date Hour Wind_speed Gust Wave Period  \
0              Spain - Nemina   15  07h         11   18  3.2     11   
1              Spain - Nemina   15  09h         10   17  3.2     11   
2              Spain - Nemina   15  11h          9   15  3.3     11   
3              Spain - Nemina   15  13h         10   15  3.3     11   
4              Spain - Nemina   15  15h          7   11  3.4     11   
5              Spain - Nemina   15  17h          7   13  3.4     11   
6              Spain - Nemina   15  19h          5    8  3.4     11   
7              Spain - Nemina   15  21h          7   11  3.3     11   
8              Spain - Nemina   16  03h          5    7  3.2     11   
9              Spain - Nemina   16  05h          6    9  3.1     11   
10             Spain - Nemina   16  07h          8   10    3     11   
11             Spain - Nemina   16  09h          9   15  2.9     10   
12             Spain - Nemina   16  11h         12   21  2.8     10   
13             Spain - Nemina   16  13h         11   17  2.7     10   
14             Spain - Nemina   16  15h         12   18  2.5     10   
15             Spain - Nemina   16  17h         11   21  2.3     10   
16             Spain - Nemina   16  19h          9   19  2.1      9   
17             Spain - Nemina   16  21h          8   15  1.9      9   
18             Spain - Nemina   17  03h          5    9  1.5      9   
19             Spain - Nemina   17  05h          5    9  1.4      9   
20             Spain - Nemina   17  07h          6   10  1.3      8   
21             Spain - Nemina   17  09h          6   10  1.2      8   
22             Spain - Nemina   17  11h          7   12  1.1      8   
23             Spain - Nemina   17  13h          8   15  1.1      8   
24             Spain - Nemina   17  15h          9   15    1     14   
25             Spain - Nemina   17  17h         10   17  1.1     14   
26             Spain - Nemina   17  19h         12   19  1.3     14   
27             Spain - Nemina   17  21h         15   26  1.4     13   
28             Spain - Nemina   18  03h         24   43  2.7      7   
29             Spain - Nemina   18  05h         25   47  3.3      8   
30             Spain - Nemina   18  07h         27   49  3.5      8   
31             Spain - Nemina   18  09h         28   51  3.7      8   
32             Spain - Nemina   18  11h         27   49  3.8      9   
33             Spain - Nemina   18  13h         26   48  3.8      9   
34             Spain - Nemina   18  15h         25   43  3.9      9   
35             Spain - Nemina   18  17h         26   43  4.1     10   
36             Spain - Nemina   18  19h         29   47  4.2     10   
37             Spain - Nemina   18  22h         32   51  4.7     10   
38             Spain - Nemina   19  04h         36   57  5.8     11   
39             Spain - Nemina   19  06h         35   56  5.9     11   
40             Spain - Nemina   19  08h         34   54  5.9     11   
41             Spain - Nemina   19  10h         32   53  5.9     11   
42             Spain - Nemina   19  12h         32   51  5.9     11   
43             Spain - Nemina   19  14h         31   49  5.8     12   
44             Spain - Nemina   19  16h         30   46  5.5     13   
45             Spain - Nemina   19  18h         26   44  5.5     13   
46             Spain - Nemina   19  20h         24   40  5.3     13   
47             Spain - Nemina   19  22h         22   33    5     13   
48             Spain - Nemina   20  04h         17   30  4.4     13   
49             Spain - Nemina   20  06h         14   25  4.3     13   
50             Spain - Nemina   20  08h         12   19  4.1     13   
51             Spain - Nemina   20  10h         11   17  3.9     12   
52             Spain - Nemina   20  12h          8   12  3.8     12   
53             Spain - Nemina   20  14h         13   16  3.8     12   
54             Spain - Nemina   20  16h         13   17  3.8     12   
55             Spain - Nemina   20  18h         

In [44]:
playasO.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasO.csv', index=False, index_label=False)


In [45]:
linksSO=['https://www.windguru.cz/501074',
         'https://www.windguru.cz/48745',
        'https://www.windguru.cz/48748',
        'https://www.windguru.cz/39598',
        'https://www.windguru.cz/48755',
        'https://www.windguru.cz/38193',
        'https://www.windguru.cz/48766',
        'https://www.windguru.cz/5691',
        'https://www.windguru.cz/48769',
        'https://www.windguru.cz/48780',
        'https://www.windguru.cz/48762']

In [46]:
lst_playasSO=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksSO)




[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   8 out of  11 | elapsed:  1.3min remaining:   29.5s
[Parallel(n_jobs=-1)]: Done  11 out of  11 | elapsed:  1.8min finished


In [47]:
playasSO=pd.concat(lst_playasSO)
playasSO

Beach Date Hour Wind_speed Gust Wave Period  \
0      Spain - Punta del Moral   15  07h         12   20  2.5     10   
1      Spain - Punta del Moral   15  09h         11   19  2.4     11   
2      Spain - Punta del Moral   15  11h         14   19  2.4     11   
3      Spain - Punta del Moral   15  13h         12   16  2.3     11   
4      Spain - Punta del Moral   15  15h         11   14  2.2     11   
5      Spain - Punta del Moral   15  17h         14   17  2.1     11   
6      Spain - Punta del Moral   15  19h         12   16  2.1     11   
7      Spain - Punta del Moral   15  21h          7   10    2     11   
8      Spain - Punta del Moral   16  03h         11   14    2     11   
9      Spain - Punta del Moral   16  05h          9   13    2     11   
10     Spain - Punta del Moral   16  07h         10   14  1.9     11   
11     Spain - Punta del Moral   16  09h         11   19  1.9     11   
12     Spain - Punta del Moral   16  11h         13   18  1.9     11   
13     Spain - Punta del Moral   16  13h         14   18  1.9     10   
14     Spain - Punta del Moral   16  15h         16   20  1.9     10   
15     Spain - Punta del Moral   16  17h         13   18  1.9     10   
16     Spain - Punta del Moral   16  19h         14   19  1.8     10   
17     Spain - Punta del Moral   16  21h         11   14  1.6     10   
18     Spain - Punta del Moral   17  03h          6    8  1.3     10   
19     Spain - Punta del Moral   17  05h          4    6  1.2      9   
20     Spain - Punta del Moral   17  07h          4    5  1.1      9   
21     Spain - Punta del Moral   17  09h          4    5    1      9   
22     Spain - Punta del Moral   17  11h          4    5  0.9      9   
23     Spain - Punta del Moral   17  13h          3    4  0.8      9   
24     Spain - Punta del Moral   17  15h          5    5  0.8      9   
25     Spain - Punta del Moral   17  17h          5    6  0.7      8   
26     Spain - Punta del Moral   17  19h          5    6  0.7      8   
27     Spain - Punta del Moral   17  21h          5    6  0.7      8   
28     Spain - Punta del Moral   18  03h          4    5  0.6      8   
29     Spain - Punta del Moral   18  05h          6    8  0.5      8   
30     Spain - Punta del Moral   18  07h          8   10  0.5      8   
31     Spain - Punta del Moral   18  09h          9   12  0.5      7   
32     Spain - Punta del Moral   18  11h         10   13  0.5      7   
33     Spain - Punta del Moral   18  13h         10   13  0.5      7   
34     Spain - Punta del Moral   18  15h          9   11  0.5      5   
35     Spain - Punta del Moral   18  17h          7    8  0.5      4   
36     Spain - Punta del Moral   18  19h          7    8  0.5      4   
37     Spain - Punta del Moral   18  22h          9   14  0.7      3   
38     Spain - Punta del Moral   19  04h         14   20  1.4      6   
39     Spain - Punta del Moral   19  06h         14   21  1.5      6   
40     Spain - Punta del Moral   19  08h         15   21  1.6      6   
41     Spain - Punta del Moral   19  10h         15   22  1.8      6   
42     Spain - Punta del Moral   19  12h         16   23  1.8      6   
43     Spain - Punta del Moral   19  14h         17   22  1.8      9   
44     Spain - Punta del Moral   19  16h         16   21  1.7     14   
45     Spain - Punta del Moral   19  18h         17   24  1.8     12   
46     Spain - Punta del Moral   19  20h         18   26  1.9     11   
47     Spain - Punta del Moral   19  22h         18   26  1.9     11   
48     Spain - Punta del Moral   20  04h         19   28  2.1      6   
49     Spain - Punta del Moral   20  06h         16   22  2.2      6   
50     Spain - Punta del Moral   20  08h         17   26  2.2      8   
51     Spain - Punta del Moral   20  10h         18   26  2.1     13   
52     Spain - Punta del Moral   20  12h         18   27  2.3      9   
53     Spain - Punta del Moral   20  14h         16   22  2.4      7   
54     Spain - Punta del Moral   20  16h         15   27  2.3    

In [48]:
playasSO.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasSO.csv', index=False, index_label=False)

In [59]:


linksE=[#'https://www.windguru.cz/501057',
       #'https://www.windguru.cz/501050',
       #'https://www.windguru.cz/42069',
       #'https://www.windguru.cz/48878',
       #'https://www.windguru.cz/48879',
       #'https://www.windguru.cz/48846',
       #'https://www.windguru.cz/501038',
       #'https://www.windguru.cz/48869',
       #'https://www.windguru.cz/48851',
       #'https://www.windguru.cz/48890',
       #'https://www.windguru.cz/48882',
       'https://www.windguru.cz/48899',
       'https://www.windguru.cz/48897',
       'https://www.windguru.cz/48908']
       #'https://www.windguru.cz/48909']   

linksS=['https://www.windguru.cz/48790',
       'https://www.windguru.cz/48816',
       'https://www.windguru.cz/48817',
       'https://www.windguru.cz/501058',
       'https://www.windguru.cz/48819',
       'https://www.windguru.cz/48811',
       'https://www.windguru.cz/48806']

linksCS=['https://www.windguru.cz/49354',
        'https://www.windguru.cz/49355',
        'https://www.windguru.cz/208234',
        'https://www.windguru.cz/49353',
        'https://www.windguru.cz/49346',
        'https://www.windguru.cz/49333',
        'https://www.windguru.cz/49332']

In [60]:
lst_playasCS=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksCS)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   7 out of   7 | elapsed:  1.3min finished


In [61]:
playasCS=pd.concat(lst_playasCS)
playasCS

Beach Date Hour Wind_speed Gust Wave Period  \
0         Spain - Las Americas   15  06h          6    9  1.4     12   
1         Spain - Las Americas   15  08h          7    9  1.4     12   
2         Spain - Las Americas   15  10h          9   10  1.5     12   
3         Spain - Las Americas   15  12h         13   12  1.5     12   
4         Spain - Las Americas   15  14h         12   13  1.6     12   
5         Spain - Las Americas   15  16h         13   14  1.5     12   
6         Spain - Las Americas   15  18h         14   16  1.6     12   
7         Spain - Las Americas   15  20h          5    7  1.6     12   
8         Spain - Las Americas   15  22h          8    9  1.5     12   
9         Spain - Las Americas   16  03h          5    5  1.5     12   
10        Spain - Las Americas   16  05h          4    6  1.6     12   
11        Spain - Las Americas   16  07h          5    7  1.7     12   
12        Spain - Las Americas   16  09h          5    5  1.7     13   
13        Spain - Las Americas   16  11h          8    9  1.7     14   
14        Spain - Las Americas   16  13h          8    8  1.7     13   
15        Spain - Las Americas   16  15h          5    5  1.6     13   
16        Spain - Las Americas   16  17h          4    4  1.6     13   
17        Spain - Las Americas   16  19h          4    4  1.5     13   
18        Spain - Las Americas   16  21h          8    8  1.4     13   
19        Spain - Las Americas   17  03h          6    7  1.2     13   
20        Spain - Las Americas   17  05h          5    7  1.1     13   
21        Spain - Las Americas   17  07h          5    7  1.1     13   
22        Spain - Las Americas   17  09h          5    8    1     13   
23        Spain - Las Americas   17  11h          8   10    1     13   
24        Spain - Las Americas   17  13h          9   10    1     13   
25        Spain - Las Americas   17  15h          7    8  0.9     13   
26        Spain - Las Americas   17  17h          7    8  0.9     13   
27        Spain - Las Americas   17  19h          5    7  0.8     13   
28        Spain - Las Americas   17  21h          6    8  0.8     13   
29        Spain - Las Americas   18  03h          8   11  0.7     12   
30        Spain - Las Americas   18  05h          9   12  0.7     12   
31        Spain - Las Americas   18  09h          5    8  0.7     12   
32        Spain - Las Americas   18  12h          8   10  0.6     12   
33        Spain - Las Americas   18  15h          7   10  0.6     12   
34        Spain - Las Americas   18  18h          4    7  0.7     18   
35        Spain - Las Americas   18  21h          3    6  0.8     17   
36        Spain - Las Americas   19  03h          2    3    1     16   
37        Spain - Las Americas   19  06h          2    3    1     16   
38        Spain - Las Americas   19  09h          1    2    1     15   
39        Spain - Las Americas   19  12h          4    5  1.1     15   
40        Spain - Las Americas   19  15h          6    8  1.1     15   
41        Spain - Las Americas   19  18h          5    7    1     15   
42        Spain - Las Americas   19  21h          3    7    1     14   
43        Spain - Las Americas   20  03h          4    5    1     14   
44        Spain - Las Americas   20  06h          2    3    1     14   
45        Spain - Las Americas   20  09h          2    3  0.9     13   
46        Spain - Las Americas   20  12h          3    4  0.9     13   
47        Spain - Las Americas   20  15h          4    4  0.9     13   
48        Spain - Las Americas   20  18h          1    3  0.8     12   
49        Spain - Las Americas   20  21h          2    4  0.8     12   
50        Spain - Las Americas   21  03h          3    5  0.8     12   
51        Spain - Las Americas   21  06h          2    3  0.8     13   
52        Spain - Las Americas   21  09h          2    5  0.9     12   
53        Spain - Las Americas   21  12h          4    6    1     18   
54        Spain - Las Americas   21  15h          3    5    1    

In [62]:
lst_playasS=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksS)

In [63]:
#playasS1=pd.concat(lst_playasS)
#playasS1

In [56]:
playasCS.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasCS.csv', index=False, index_label=False)

In [64]:
lst_playasE=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksE)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   1 out of   1 | elapsed:   40.1s finished


In [65]:
playasE=pd.concat(lst_playasE)


In [58]:
playasE.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasE.csv', index=False, index_label=False)